In [0]:
spark.conf.set("fs.azure.account.key.weatherdatastorage09.dfs.core.windows.net", "B2bEeFnUp3PZ3F30/WS4303QZSBtriz3pc4ntFa6cH5kbSALhzmK8YLN1wCUrpTNjGoVSQXNZQH8+ASt+5Nm4w==")
raw_path = "abfss://bronzelayer@weatherdatastorage09.dfs.core.windows.net/weather_raw/"

In [0]:
account   = "weatherdatastorage09"
container = "bronzelayer"
raw_dir   = "weather_raw"       
key       = "B2bEeFnUp3PZ3F30/WS4303QZSBtriz3pc4ntFa6cH5kbSALhzmK8YLN1wCUrpTNjGoVSQXNZQH8+ASt+5Nm4w=="

spark.conf.set(f"fs.azure.account.auth.type.{account}.dfs.core.windows.net", "SharedKey")
spark.conf.set(f"fs.azure.account.key.{account}.dfs.core.windows.net",  key)

raw_path    = f"abfss://{container}@{account}.dfs.core.windows.net/{raw_dir}/"
bronze_path = f"abfss://{container}@{account}.dfs.core.windows.net/bronze"


In [0]:
from pyspark.sql.functions import col, current_timestamp

def copy_to_bronze(csv):
    (
        spark.read          
             .option("header", "true")
             .option("inferSchema", "true")
             .csv(raw_path + csv)
             .withColumn("source_file", col("_metadata.file_path"))
             .withColumn("ingestion_time", current_timestamp())
             .write
             .format("delta")
             .option("delta.columnMapping.mode", "name") 
             .mode("overwrite") 
             .save(f"{bronze_path}/{csv}")
    )

csv_files = [
    "city_attributes.csv", "humidity.csv", "pressure.csv", "temperature.csv",
    "weather_description.csv", "wind_direction.csv", "wind_speed.csv"
]

for f in csv_files:
    copy_to_bronze(f)

In [0]:
from pyspark.sql.functions import col, expr
from pyspark.sql.types import StringType
import pyspark.sql.functions as F

humidity_df = spark.read.format("delta").load(f"{bronze_path}/humidity.csv")
temperature_df = spark.read.format("delta").load(f"{bronze_path}/temperature.csv")

city_cols = [c for c in humidity_df.columns if c not in ['datetime', 'ingestion_time', 'source_file']]

humidity_long = humidity_df.selectExpr("datetime", *[f"`{city}` as `{city}`" for city in city_cols]) \
    .selectExpr("datetime", "stack(" + str(len(city_cols)) + ", " + 
                ", ".join([f"'{c}', `{c}`" for c in city_cols]) + 
                ") as (location, humidity)")

temperature_long = temperature_df.selectExpr("datetime", *[f"`{city}` as `{city}`" for city in city_cols]) \
    .selectExpr("datetime", "stack(" + str(len(city_cols)) + ", " + 
                ", ".join([f"'{c}', `{c}`" for c in city_cols]) + 
                ") as (location, temperature)")

silver_df = humidity_long.join(
    temperature_long, ["datetime", "location"]
)

silver_path = f"abfss://{container}@{account}.dfs.core.windows.net/silverlayer"
silver_df.write.format("delta").mode("overwrite").save(f"{silver_path}/weather_combined")

silver_df.display(5)

datetime location humidity temperature 2014-07-18T08:00:00Z Vancouver 82.0 289.41 2014-07-18T09:00:00Z Vancouver 82.0 288.71 2014-07-18T10:00:00Z Vancouver 87.0 287.78 2014-07-18T11:00:00Z Vancouver 87.0 287.52 2014-07-18T12:00:00Z Vancouver 93.0 286.84 2014-07-18T13:00:00Z Vancouver 87.0 287.09 2014-07-18T14:00:00Z Vancouver 87.0 287.75 2014-07-18T15:00:00Z Vancouver 82.0 289.58 2014-07-18T16:00:00Z Vancouver 63.0 290.0 2014-07-18T17:00:00Z Vancouver 63.0 292.67 2014-07-18T18:00:00Z Vancouver 63.0 292.82 2014-07-18T19:00:00Z Vancouver 68.0 293.68 2014-07-18T20:00:00Z Vancouver 64.0 295.41 2014-07-18T21:00:00Z Vancouver 53.0 295.98 2014-07-18T22:00:00Z Vancouver 53.0 295.98 2014-07-18T23:00:00Z Vancouver 49.0 295.73 2014-07-19T00:00:00Z Vancouver 53.0 296.44 2014-07-19T01:00:00Z Vancouver 56.0 296.18 2014-07-19T02:00:00Z Vancouver 56.0 295.24 2014-07-19T03:00:00Z Vancouver 60.0 294.68 2014-07-19T04:00:00Z Vancouver 68.0 293.48 2014-07-19T05:00:00Z Vancouver 72.0 292.38 2014-07-19T06:00:00Z Vancouver 82.0 291.15 2014-07-19T07:00:00Z Vancouver 82.0 290.17 2014-07-19T08:00:00Z Vancouver 82.0 289.94 2014-07-19T09:00:00Z Vancouver 82.0 289.63 2014-07-19T10:00:00Z Vancouver 82.0 289.6 2014-07-19T11:00:00Z Vancouver 82.0 289.79 2014-07-19T12:00:00Z Vancouver 87.0 289.49 2014-07-19T13:00:00Z Vancouver 87.0 289.17 2014-07-19T14:00:00Z Vancouver 82.0 289.77 2014-07-19T15:00:00Z Vancouver 79.0 290.12 2014-07-19T16:00:00Z Vancouver 82.0 289.6 2014-07-19T17:00:00Z Vancouver 87.0 289.77 2014-07-19T18:00:00Z Vancouver 77.0 290.78 2014-07-19T19:00:00Z Vancouver 72.0 290.58 2014-07-19T20:00:00Z Vancouver 68.0 291.44 2014-07-19T21:00:00Z Vancouver 68.0 292.43 2014-07-19T22:00:00Z Vancouver 68.0 293.39 2014-07-19T23:00:00Z Vancouver 60.0 294.06 2014-07-20T00:00:00Z Vancouver 64.0 293.88 2014-07-20T01:00:00Z Vancouver 64.0 294.9 2014-07-20T02:00:00Z Vancouver 60.0 294.67 2014-07-20T03:00:00Z Vancouver 72.0 293.53 2014-07-20T04:00:00Z Vancouver 72.0 292.18 2014-07-20T05:00:00Z Vancouver 72.0 291.29 2014-07-20T06:00:00Z Vancouver 68.0 290.9 2014-07-20T07:00:00Z Vancouver 68.0 289.37 2014-07-20T08:00:00Z Vancouver 72.0 288.95 2014-07-20T09:00:00Z Vancouver 72.0 288.78 2014-07-20T10:00:00Z Vancouver 82.0 288.39 2014-07-20T11:00:00Z Vancouver 98.0 288.13 2014-07-20T12:00:00Z Vancouver 77.0 287.96 2014-07-20T13:00:00Z Vancouver 93.0 287.16 2014-07-20T14:00:00Z Vancouver 82.0 287.37 2014-07-20T15:00:00Z Vancouver 77.0 287.51 2014-07-20T16:00:00Z Vancouver 82.0 287.95 2014-07-20T17:00:00Z Vancouver 82.0 288.0 2014-07-20T18:00:00Z Vancouver 82.0 288.11 2014-07-20T19:00:00Z Vancouver 72.0 288.57 2014-07-20T20:00:00Z Vancouver 77.0 289.08 2014-07-20T21:00:00Z Vancouver 82.0 288.86 2014-07-20T22:00:00Z Vancouver 68.0 289.97 2014-07-20T23:00:00Z Vancouver 68.0 290.58 2014-07-21T00:00:00Z Vancouver 72.0 290.7 2014-07-21T01:00:00Z Vancouver 77.0 290.76 2014-07-21T02:00:00Z Vancouver 72.0 291.29 2014-07-21T03:00:00Z Vancouver 72.0 290.34 2014-07-21T04:00:00Z Vancouver 77.0 289.43 2014-07-21T05:00:00Z Vancouver 72.0 288.96 2014-07-21T06:00:00Z Vancouver 77.0 288.33 2014-07-21T07:00:00Z Vancouver 82.0 287.84 2014-07-21T08:00:00Z Vancouver 82.0 287.6 2014-07-21T09:00:00Z Vancouver 82.0 287.57 2014-07-21T10:00:00Z Vancouver 82.0 287.41 2014-07-21T11:00:00Z Vancouver 82.0 287.37 2014-07-21T12:00:00Z Vancouver 82.0 287.43 2014-07-21T13:00:00Z Vancouver 87.0 287.02 2014-07-21T14:00:00Z Vancouver 77.0 287.24 2014-07-21T15:00:00Z Vancouver 77.0 287.44 2014-07-21T16:00:00Z Vancouver 72.0 288.78 2014-07-21T17:00:00Z Vancouver 68.0 290.52 2014-07-21T18:00:00Z Vancouver 68.0 291.73 2014-07-21T19:00:00Z Vancouver 63.0 292.18 2014-07-21T20:00:00Z Vancouver 52.0 294.2 2014-07-21T21:00:00Z Vancouver 60.0 294.61 2014-07-21T22:00:00Z Vancouver 56.0 295.12 2014-07-21T23:00:00Z Vancouver 56.0 296.22 2014-07-22T00:00:00Z Vancouver 49.0 296.17 2014-07-22T01:00:00Z Vancouver 56.0 295.98 2014-07-22T02:00:00Z Vancouver 56.0 295.46 2014-07-22T03:00:00Z Vancouver 49.0 293.49 2014-07-22T04:

In [0]:
from pyspark.sql.functions import col

# Load Silver data
silver_df = spark.read.format("delta").load(f"{silver_path}/weather_combined")

# Load pressure and wind_speed data (from bronze)
pressure_df = spark.read.format("delta").load(f"{bronze_path}/pressure.csv")
wind_speed_df = spark.read.format("delta").load(f"{bronze_path}/wind_speed.csv")

# Get city columns again (excluding metadata)
city_cols = [c for c in pressure_df.columns if c not in ['datetime', 'ingestion_time', 'source_file']]

# Unpivot pressure
pressure_long = pressure_df.selectExpr("datetime", *[f"`{city}` as `{city}`" for city in city_cols]) \
    .selectExpr("datetime", "stack(" + str(len(city_cols)) + ", " +
                ", ".join([f"'{c}', `{c}`" for c in city_cols]) +
                ") as (location, pressure)")

# Unpivot wind_speed
wind_speed_long = wind_speed_df.selectExpr("datetime", *[f"`{city}` as `{city}`" for city in city_cols]) \
    .selectExpr("datetime", "stack(" + str(len(city_cols)) + ", " +
                ", ".join([f"'{c}', `{c}`" for c in city_cols]) +
                ") as (location, wind_speed)")

# Join all into Gold
gold_df = silver_df.alias("s") \
    .join(pressure_long.alias("p"), ["datetime", "location"]) \
    .join(wind_speed_long.alias("w"), ["datetime", "location"]) \
    .select(
        "s.datetime", "s.location", "temperature", "humidity",
        "p.pressure", "w.wind_speed"
    )

# Save Gold Layer
gold_path = f"abfss://{container}@{account}.dfs.core.windows.net/goldlayer"
gold_df.write.format("delta").mode("overwrite").save(f"{gold_path}/weather_features")

gold_df.display(5)


datetime location temperature humidity pressure wind_speed 2014-07-18T08:00:00Z Vancouver 289.41 82.0 1016.0 3.0 2014-07-18T09:00:00Z Vancouver 288.71 82.0 1016.0 1.0 2014-07-18T10:00:00Z Vancouver 287.78 87.0 1016.0 3.0 2014-07-18T11:00:00Z Vancouver 287.52 87.0 1016.0 2.0 2014-07-18T12:00:00Z Vancouver 286.84 93.0 1017.0 2.0 2014-07-18T13:00:00Z Vancouver 287.09 87.0 1017.0 3.0 2014-07-18T14:00:00Z Vancouver 287.75 87.0 1017.0 2.0 2014-07-18T15:00:00Z Vancouver 289.58 82.0 1018.0 2.0 2014-07-18T16:00:00Z Vancouver 290.0 63.0 1018.0 3.0 2014-07-18T17:00:00Z Vancouver 292.67 63.0 1018.0 3.0 2014-07-18T18:00:00Z Vancouver 292.82 63.0 1018.0 3.0 2014-07-18T19:00:00Z Vancouver 293.68 68.0 1018.0 4.0 2014-07-18T20:00:00Z Vancouver 295.41 64.0 1019.0 4.0 2014-07-18T21:00:00Z Vancouver 295.98 53.0 1018.0 2.0 2014-07-18T22:00:00Z Vancouver 295.98 53.0 1018.0 4.0 2014-07-18T23:00:00Z Vancouver 295.73 49.0 1018.0 4.0 2014-07-19T00:00:00Z Vancouver 296.44 53.0 1017.0 5.0 2014-07-19T01:00:00Z Vancouver 296.18 56.0 1017.0 5.0 2014-07-19T02:00:00Z Vancouver 295.24 56.0 1016.0 5.0 2014-07-19T03:00:00Z Vancouver 294.68 60.0 1016.0 5.0 2014-07-19T04:00:00Z Vancouver 293.48 68.0 1016.0 5.0 2014-07-19T05:00:00Z Vancouver 292.38 72.0 1016.0 5.0 2014-07-19T06:00:00Z Vancouver 291.15 82.0 1016.0 6.0 2014-07-19T07:00:00Z Vancouver 290.17 82.0 1016.0 7.0 2014-07-19T08:00:00Z Vancouver 289.94 82.0 1016.0 6.0 2014-07-19T09:00:00Z Vancouver 289.63 82.0 1016.0 6.0 2014-07-19T10:00:00Z Vancouver 289.6 82.0 1015.0 6.0 2014-07-19T11:00:00Z Vancouver 289.79 82.0 1015.0 6.0 2014-07-19T12:00:00Z Vancouver 289.49 87.0 1015.0 6.0 2014-07-19T13:00:00Z Vancouver 289.17 87.0 1015.0 8.0 2014-07-19T14:00:00Z Vancouver 289.77 82.0 1015.0 6.0 2014-07-19T15:00:00Z Vancouver 290.12 79.0 1003.0 3.0 2014-07-19T16:00:00Z Vancouver 289.6 82.0 1015.0 5.0 2014-07-19T17:00:00Z Vancouver 289.77 87.0 1085.0 3.0 2014-07-19T18:00:00Z Vancouver 290.78 77.0 1014.0 5.0 2014-07-19T19:00:00Z Vancouver 290.58 72.0 1014.0 3.0 2014-07-19T20:00:00Z Vancouver 291.44 68.0 1014.0 6.0 2014-07-19T21:00:00Z Vancouver 292.43 68.0 1014.0 4.0 2014-07-19T22:00:00Z Vancouver 293.39 68.0 1014.0 5.0 2014-07-19T23:00:00Z Vancouver 294.06 60.0 1013.0 6.0 2014-07-20T00:00:00Z Vancouver 293.88 64.0 1013.0 4.0 2014-07-20T01:00:00Z Vancouver 294.9 64.0 1013.0 5.0 2014-07-20T02:00:00Z Vancouver 294.67 60.0 1013.0 3.0 2014-07-20T03:00:00Z Vancouver 293.53 72.0 1012.0 3.0 2014-07-20T04:00:00Z Vancouver 292.18 72.0 1012.0 4.0 2014-07-20T05:00:00Z Vancouver 291.29 72.0 1012.0 3.0 2014-07-20T06:00:00Z Vancouver 290.9 68.0 1012.0 3.0 2014-07-20T07:00:00Z Vancouver 289.37 68.0 1012.0 3.0 2014-07-20T08:00:00Z Vancouver 288.95 72.0 1012.0 6.0 2014-07-20T09:00:00Z Vancouver 288.78 72.0 1012.0 6.0 2014-07-20T10:00:00Z Vancouver 288.39 82.0 1012.0 5.0 2014-07-20T11:00:00Z Vancouver 288.13 98.0 1012.0 1.0 2014-07-20T12:00:00Z Vancouver 287.96 77.0 1013.0 6.0 2014-07-20T13:00:00Z Vancouver 287.16 93.0 1014.0 1.0 2014-07-20T14:00:00Z Vancouver 287.37 82.0 1013.0 1.0 2014-07-20T15:00:00Z Vancouver 287.51 77.0 1014.0 4.0 2014-07-20T16:00:00Z Vancouver 287.95 82.0 1014.0 3.0 2014-07-20T17:00:00Z Vancouver 288.0 82.0 1014.0 3.0 2014-07-20T18:00:00Z Vancouver 288.11 82.0 1014.0 3.0 2014-07-20T19:00:00Z Vancouver 288.57 72.0 1015.0 2.0 2014-07-20T20:00:00Z Vancouver 289.08 77.0 1015.0 3.0 2014-07-20T21:00:00Z Vancouver 288.86 82.0 1015.0 3.0 2014-07-20T22:00:00Z Vancouver 289.97 68.0 1015.0 1.0 2014-07-20T23:00:00Z Vancouver 290.58 68.0 1014.0 2.0 2014-07-21T00:00:00Z Vancouver 290.7 72.0 1014.0 2.0 2014-07-21T01:00:00Z Vancouver 290.76 77.0 1014.0 1.0 2014-07-21T02:00:00Z Vancouver 291.29 72.0 1014.0 1.0 2014-07-21T03:00:00Z Vancouver 290.34 72.0 1014.0 1.0 2014-07-21T04:00:00Z Vancouver 289.43 77.0 1014.0 1.0 2014-07-21T05:00:00Z Vancouver 288.96 72.0 1014.0 3.0 2014-07-21T06:00:00Z Vancouver 288.33 77.0 1014.0 3.0 2014-07-21T07:00:00Z Vancouver 287.84 82.0 1014.0 3.0 2014-07-21T08:00:00Z Vancouver 287.6 82.0 1015.0 4.0 2014-07